In [1]:
cd ../../../

/Users/mykhailoslukvin/repo/dv-data-pipeline


/Users/mykhailoslukvin/.local/lib/python3.11/site-packages/IPython/core/magics/osm.py:417: UserWarning: This is now an optional IPython functionality, setting dhist requires you to install the `pickleshare` library.
  self.shell.db['dhist'] = compress_dhist(dhist)[-100:]


In [52]:
from urllib.parse import urlparse
from io import BytesIO
import pandas as pd

from dfpp.storage import StorageManager
from dfpp.transformation.column_name_template import ensure_canonical_columns, sort_columns_canonically
from dfpp.publishing import publish_series

In [3]:
SOURCE_NAME = "GLOBAL_PI"

In [ ]:
async with StorageManager() as storage_manager:
    indicator_cfgs = await storage_manager.get_indicators_cfg(
        indicator_ids=None, contain_filter=None
    )
    source_cfgs = await storage_manager.get_sources_cfgs()

2024-11-10 19:04:22,383 - INFO - _universal - Request URL: 'https://sdgigeneralstorage.blob.core.windows.net/dfx-etl-pipeline-dev?restype=REDACTED&comp=REDACTED&prefix=REDACTED&sv=REDACTED&st=REDACTED&se=REDACTED&sr=REDACTED&sp=REDACTED&sig=REDACTED'
Request method: 'GET'
Request headers:
    'x-ms-version': 'REDACTED'
    'Accept': 'application/xml'
    'x-ms-date': 'REDACTED'
    'x-ms-client-request-id': 'd4f08972-9f85-11ef-aeba-acbc327b2b3d'
    'User-Agent': 'azsdk-python-storage-blob/12.21.0 Python/3.11.9 (macOS-10.16-x86_64-i386-64bit)'
No body was attached to the request
2024-11-10 19:04:23,394 - INFO - _universal - Response status: 200
Response headers:
    'Transfer-Encoding': 'chunked'
    'Content-Type': 'application/xml'
    'Server': 'Windows-Azure-Blob/1.0 Microsoft-HTTPAPI/2.0'
    'x-ms-request-id': '975fc050-e01e-0039-4292-335435000000'
    'x-ms-client-request-id': 'd4f08972-9f85-11ef-aeba-acbc327b2b3d'
    'x-ms-version': 'REDACTED'
    'Access-Control-Expose-Header

In [5]:
df_indicator = pd.DataFrame(indicator_cfgs)
df_source = pd.DataFrame(source_cfgs)

In [ ]:
df_source = df_source[
    (df_source.source_type == "Manual") & (df_source.id == SOURCE_NAME)
]

df_join = df_source.merge(df_indicator, left_on="id", right_on="source_id")

In [ ]:
config_columns = [
    "id",
    "name",
    "url",
    "indicator_id",
    "indicator_name",
    "sheet_name",
    "group_name",
    "value_column",
    "value_col",
]

In [34]:
column_to_indicator_map = dict(df_join[["indicator_id", "value_column"]].values)
indicator_to_column_map = dict(df_join[["value_column", "indicator_id"]].values)
indicator_to_name_map = dict(df_join[["indicator_id", "indicator_name"]].values)

In [35]:
len(column_to_indicator_map)

24

In [67]:
async with StorageManager() as storage_manager:
    series_bytes = await storage_manager.read_blob(path="backup/sources/GLOBAL_PI.csv")
    df_source = pd.read_csv(BytesIO(series_bytes))
df = df_source.copy()

2024-11-10 19:43:03,621 - INFO - _universal - Request URL: 'https://sdgigeneralstorage.blob.core.windows.net/dfx-etl-pipeline-dev/backup/sources/GLOBAL_PI.csv?sv=REDACTED&st=REDACTED&se=REDACTED&sr=REDACTED&sp=REDACTED&sig=REDACTED'
Request method: 'HEAD'
Request headers:
    'x-ms-version': 'REDACTED'
    'Accept': 'application/xml'
    'x-ms-date': 'REDACTED'
    'x-ms-client-request-id': '3c8247b0-9f8b-11ef-aeba-acbc327b2b3d'
    'User-Agent': 'azsdk-python-storage-blob/12.21.0 Python/3.11.9 (macOS-10.16-x86_64-i386-64bit)'
No body was attached to the request
2024-11-10 19:43:04,062 - INFO - _universal - Response status: 200
Response headers:
    'Content-Length': '32399'
    'Content-Type': 'text/csv'
    'Content-MD5': 'REDACTED'
    'Last-Modified': 'Sun, 10 Nov 2024 17:41:48 GMT'
    'Accept-Ranges': 'REDACTED'
    'Etag': '"0x8DD01AEF3C9250B"'
    'Server': 'Windows-Azure-Blob/1.0 Microsoft-HTTPAPI/2.0'
    'x-ms-request-id': '1bc8ddae-801e-0062-7d97-336d0e000000'
    'x-ms-cli

In [68]:
df = df.rename(columns={"code": "alpha_3_code"})
df.drop(columns=["name",], inplace=True)

In [69]:
df = df.melt(id_vars=["alpha_3_code", "year"], value_name="value", var_name="series_id")

In [70]:
df = df[df.series_id.isin(column_to_indicator_map.values())]

In [71]:
df["series_id"] = df["series_id"].replace(indicator_to_column_map)

In [75]:
df["series_name"] = df["series_id"].replace(indicator_to_name_map)
df["source"] = "https://www.economicsandpeace.org/"

In [76]:
df = ensure_canonical_columns(df)
df = sort_columns_canonically(df)

In [77]:
for series_id, df_series in df.groupby("series_id"): 
    await publish_series(series_id, df_series, source_folder=SOURCE_NAME)

2024-11-10 19:44:26,156 - INFO - _universal - Request URL: 'https://sdgigeneralstorage.blob.core.windows.net/dfx-etl-pipeline-dev/test/GLOBAL_PI/xlsx/accesstosmallweapons_globalpi.xlsx?sv=REDACTED&st=REDACTED&se=REDACTED&sr=REDACTED&sp=REDACTED&sig=REDACTED'
Request method: 'PUT'
Request headers:
    'Content-Length': '11687'
    'x-ms-blob-type': 'REDACTED'
    'x-ms-version': 'REDACTED'
    'Content-Type': 'application/octet-stream'
    'Accept': 'application/xml'
    'x-ms-date': 'REDACTED'
    'x-ms-client-request-id': '6db40ed6-9f8b-11ef-aeba-acbc327b2b3d'
    'User-Agent': 'azsdk-python-storage-blob/12.21.0 Python/3.11.9 (macOS-10.16-x86_64-i386-64bit)'
A body is sent with the request
2024-11-10 19:44:26,591 - INFO - _universal - Response status: 201
Response headers:
    'Content-Length': '0'
    'Content-MD5': 'REDACTED'
    'Last-Modified': 'Sun, 10 Nov 2024 17:44:26 GMT'
    'Etag': '"0x8DD01AF52387CE1"'
    'Server': 'Windows-Azure-Blob/1.0 Microsoft-HTTPAPI/2.0'
    'x-ms-r